In [61]:
import cv2
import os, sys
import json
import time
import skimage.io
import numpy as np

In [2]:
# Root directory of the project
ROOT_DIR = os.path.abspath("../")
# Import Mask RCNN
sys.path.append(ROOT_DIR)  # To find local version of the library
from mrcnn import utils
import mrcnn.model as modellib
from mrcnn import visualize
# Import COCO config
# sys.path.append(os.path.join(ROOT_DIR, "samples/coco/"))  # To find local version
# import coco
# Import COCO config
sys.path.append(os.path.join(ROOT_DIR, "samples/coco/"))  # To find local version
import coco

Using TensorFlow backend.


In [24]:
def detectColour(image, aoi, threshold=0.3 ):
    # define the list of boundaries
    boundaries = [ #RGB
        ([100, 50, 50], [255, 130, 130], 'RED'),
        ([50, 100, 50], [130, 255, 130], 'GREEN'),
        ([50, 50, 100], [130, 130, 255], 'BLUE'),
        ([100, 100, 50], [255, 255, 130], 'YELLOW' ),
        ([100, 100, 100], [225, 225, 225], 'GREY' ), 
        ([225, 225, 225], [255, 255, 255], 'WHITE' ) 
    ]
    # loop over the boundaries
    for (lower, upper, colour) in boundaries:
    # (lower, upper, colour) = boundaries[4]
        # create NumPy arrays from the boundaries
        lower = np.array(lower, dtype = "uint8")
        upper = np.array(upper, dtype = "uint8")

        # find the colors within the specified boundaries and apply
        # the mask
        mask = cv2.inRange(image, lower, upper)

        tmp_mask = np.logical_and(mask, aoi)
        output = cv2.bitwise_and(image, image, mask = tmp_mask.astype("uint8"))
        # print(np.sum(np.logical_and(mask, aoi))/np.sum(aoi))
        isColour = np.sum(np.logical_and(mask, aoi))/np.sum(aoi) > threshold
        if isColour:
            return colour, output
            
    return "OTHERS", output

In [60]:
def getImageIdfrmPath(path, case='oneMotoring'):
    image_id = ''
    # for onemotoring:
    if case.lower() == 'oneMotoring'.lower():
        path, im = os.path.split(path)
        path, date = os.path.split(path)
        path, location = os.path.split(path)
        image_id = location.replace(' ', '_') + '-' + date + '-' + im.replace('.jpeg','')
    return image_id

In [4]:

# Directory to save logs and trained model
MODEL_DIR = os.path.join(ROOT_DIR, "logs")

# Local path to trained weights file
COCO_MODEL_PATH = os.path.join(ROOT_DIR, "mask_rcnn_coco.h5")
# Download COCO trained weights from Releases if needed
if not os.path.exists(COCO_MODEL_PATH):
    utils.download_trained_weights(COCO_MODEL_PATH)

class InferenceConfig(coco.CocoConfig):
    # Set batch size to 1 since we'll be running inference on
    # one image at a time. Batch size = GPU_COUNT * IMAGES_PER_GPU
    GPU_COUNT = 1
    IMAGES_PER_GPU = 1

config = InferenceConfig()
config.display()

# Create model object in inference mode.
model = modellib.MaskRCNN(mode="inference", model_dir=MODEL_DIR, config=config)

# Load weights trained on MS-COCO
model.load_weights(COCO_MODEL_PATH, by_name=True)

# COCO Class names
# Index of the class in the list is its ID. For example, to get ID of
# the teddy bear class, use: class_names.index('teddy bear')
class_names = ['BG', 'person', 'bicycle', 'car', 'motorcycle', 'airplane',
               'bus', 'train', 'truck', 'boat', 'traffic light',
               'fire hydrant', 'stop sign']


Configurations:
BACKBONE                       resnet101
BACKBONE_STRIDES               [4, 8, 16, 32, 64]
BATCH_SIZE                     1
BBOX_STD_DEV                   [0.1 0.1 0.2 0.2]
COMPUTE_BACKBONE_SHAPE         None
DETECTION_MAX_INSTANCES        100
DETECTION_MIN_CONFIDENCE       0.7
DETECTION_NMS_THRESHOLD        0.3
FPN_CLASSIF_FC_LAYERS_SIZE     1024
GPU_COUNT                      1
GRADIENT_CLIP_NORM             5.0
IMAGES_PER_GPU                 1
IMAGE_CHANNEL_COUNT            3
IMAGE_MAX_DIM                  1024
IMAGE_META_SIZE                93
IMAGE_MIN_DIM                  800
IMAGE_MIN_SCALE                0
IMAGE_RESIZE_MODE              square
IMAGE_SHAPE                    [1024 1024    3]
LEARNING_MOMENTUM              0.9
LEARNING_RATE                  0.001
LOSS_WEIGHTS                   {'rpn_class_loss': 1.0, 'rpn_bbox_loss': 1.0, 'mrcnn_class_loss': 1.0, 'mrcnn_bbox_loss': 1.0, 'mrcnn_mask_loss': 1.0}
MASK_POOL_SIZE                 14
MASK_SHAPE         

In [58]:
DIR = "C:\\Users\\Xin Yan\\Documents\\work\\ds\\downloads\\one_motoring_wk1\\"
output_file = "C:\\Users\\Xin Yan\\Documents\\work\\ds\\downloads\\one_motoring_wk1\\rcnn_generated2.json"
folders = os.listdir(DIR)
OBJECTS_OF_INTEREST_ls = [2, 3, 4, 6, 7, 8, 10, 12]

json_output = ''
global_counter = 1
# TODO remove multilayer for loops and list all images first.
# TODO track what has been tested and the global counter.
list_of_image_paths = []
for path, subdirs, files in os.walk(DIR):
    for file in files:
        if file.endswith('.jpeg'):
            list_of_image_paths.append(os.path.join(path,file))
            
start = time.time()            
for counter, each_image_path in enumerate(list_of_image_paths):
    if each_image_path is in done_list:
        continue
    image = skimage.io.imread(each_image_path)
    image_id = getImageIdfrmPath(each_image_path)
    
    test_results = model.detect([image], verbose=0)
    r = test_results[0]

    for idx, roi in enumerate(r['rois']):
        if len(OBJECTS_OF_INTEREST_ls) != 0 and r['class_ids'][idx] not in OBJECTS_OF_INTEREST_ls:
            continue
        y1, x1, y2, x2 = roi
        aoi = r['masks'][y1:y2, x1:x2,idx]
        input = image[y1:y2, x1:x2]
        colour, _ = detectColour(input, aoi)

        bbox = [int(x1), int(y1), int(x2-x1), int(y2-y1)]  # may need to normalise and change to float for beaverdam
        cat_id = class_names[r['class_ids'][idx]].upper()

        ann = {'bbox': bbox, 'category_id': cat_id+", "+colour, "id": str(global_counter),"image_id": image_id}
        global_counter+=1
        if json_output != '':
            json_output += ', '
        json_output += json.dumps(ann)
    
    if ((counter % 100)==0):
        print(string(counter) + ' images done. ' + str(len(list_of_image_paths)-counter) + ' more to go. Hang in there!')
    
    if len(r['rois'])==0:
        print('Nothing detected in image with id: '+ image_id)

 
if json_output == '':
    print('Nothing detected.')
else:
    print(json_output)
json_output = '{\"annotations\": ['+ json_output + ']}'

File = open(output_file,'w')
File.write(json_output)
File.close()

end = time.time()
print(end - start)

Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.1

Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.1

Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.1

Nothing detected in image with id: AYE_-_View_from_After_Tuas_West_Road-20190117-20190117T071302.188
Processing 1 images
image                    shape: (288, 352, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Nothing detected in image with id: AYE_-_View_from_After_Tuas_West_Road-20190117-20190117T143517.664
Processing 1 images
image                    shape: (288, 352, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  fl

Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.1

...

molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anch

anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255

molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anch

Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
Processing 1 images
image                    shape: (480, 640, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.1

KeyboardInterrupt: 

In [50]:
json_output

'{"bbox": [445, 183, 58, 33], "category_id": "CAR, OTHER", "id": 1, "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083321.155"}, {"bbox": [405, 195, 19, 22], "category_id": "MOTORCYCLE, OTHER", "id": 2, "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083821.063"}, {"bbox": [187, 88, 46, 47], "category_id": "TRUCK, OTHER", "id": 3, "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083821.063"}, {"bbox": [251, 88, 70, 64], "category_id": "TRUCK, OTHER", "id": 4, "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083821.063"}, {"bbox": [276, 239, 52, 45], "category_id": "CAR, OTHER", "id": 5, "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T084320.955"}, {"bbox": [404, 224, 21, 27], "category_id": "PERSON, OTHER", "id": 6, "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T084320.955"}, {"bbox": [405, 237, 22, 22], "category_id": "MOTORCYCLE, OTHER", "id": 7, "image_id": "AYE_-_

In [63]:
tmp = json_output.replace(', \"image_id\"','\", \"image_id\"')
File = open("C:\\Users\\Xin Yan\\Documents\\work\\ds\\downloads\\one_motoring_wk1\\rcnn_generated2.json",'w')
File.write(tmp)
File.close()

In [105]:
'{\"annotations\": [' + tmp[0:20] + ']}'

'{"annotations": [{"bbox": [445, 183, ]}'

In [106]:
k = json.loads('{\"annotations\": ['+ tmp + ']}')
tmp2 = json.dumps(k)
print(type(tmp))
print(type(tmp2))


<class 'str'>
<class 'str'>


'"{\\"bbox\\": [445, 183, 58, 33], \\"category_id\\": \\"CAR, OTHER\\", \\"id\\": \\"1\\", \\"image_id\\": \\"AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083321.155\\"},"'

In [91]:
tmp

'{"bbox": [445, 183, 58, 33], "category_id": "CAR, OTHER", "id": "1", "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083321.155"}, {"bbox": [405, 195, 19, 22], "category_id": "MOTORCYCLE, OTHER", "id": "2", "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083821.063"}, {"bbox": [187, 88, 46, 47], "category_id": "TRUCK, OTHER", "id": "3", "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083821.063"}, {"bbox": [251, 88, 70, 64], "category_id": "TRUCK, OTHER", "id": "4", "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T083821.063"}, {"bbox": [276, 239, 52, 45], "category_id": "CAR, OTHER", "id": "5", "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T084320.955"}, {"bbox": [405, 237, 22, 22], "category_id": "MOTORCYCLE, OTHER", "id": "6", "image_id": "AYE_-_View_from_After_Tuas_West_Road-20190110-20190110T084320.955"}, {"bbox": [268, 288, 20, 32], "category_id": "MOTORCYCLE, OTHER", "id": "7", "

In [80]:
for each_folder in folders:
    if not os.path.isdir(os.path.join(DIR, each_folder)):
            continue
    sub_folders = os.listdir(os.path.join(DIR, each_folder))
    for each_sub_folder in sub_folders:
        if not os.path.isdir(os.path.join(DIR, each_folder,each_sub_folder)):
            continue
        images = [file for file in os.listdir(os.path.join(DIR, each_folder,each_sub_folder)) if file.endswith(".jpeg")]
        for each_image in images:

SyntaxError: unexpected EOF while parsing (<ipython-input-80-637d7c9f86de>, line 9)

In [98]:
ref_file = open("C:\\Users\\Xin Yan\\Documents\\work\\ds\\downloads\\one_motoring_wk1\\rcnn_generated2.json",'r')
ref_input = ref_file.read()
ref_json = json.loads(ref_input)

In [ ]:
for each_folder in folders:
    if not os.path.isdir(os.path.join(DIR, each_folder)):
            continue
    sub_folders = os.listdir(os.path.join(DIR, each_folder))
    for each_sub_folder in sub_folders:
        if not os.path.isdir(os.path.join(DIR, each_folder,each_sub_folder)):
            continue
        images = [file for file in os.listdir(os.path.join(DIR, each_folder,each_sub_folder)) if file.endswith(".jpeg")]
        for each_image in images:
            image = skimage.io.imread(os.path.join(DIR, each_folder, each_sub_folder, each_image))
            image_id = each_folder.replace(' ','_')+'-'+each_sub_folder+'-'+each_image.replace('.jpeg','')
            test_results = model.detect([image], verbose=1)  # TODO change to non verbose
            r = test_results[0]

            for idx, roi in enumerate(r['rois']):
                if len(OBJECTS_OF_INTEREST_ls) != 0 and r['class_ids'][idx] not in OBJECTS_OF_INTEREST_ls:
                    continue
                y1, x1, y2, x2 = roi
                aoi = r['masks'][y1:y2, x1:x2,idx]
                input = image[y1:y2, x1:x2]
                colour, _ = detectColour(input, aoi)

                bbox = [int(x1), int(y1), int(x2-x1), int(y2-y1)]  # may need to normalise and change to float for beaverdam
                cat_id = class_names[r['class_ids'][idx]].upper()

                ann = {'bbox': bbox, 'category_id': cat_id+", "+colour, "id": str(global_counter),"image_id": image_id}
                global_counter+=1
                if json_output != '':
                    json_output += ', '
                json_output += json.dumps(ann)

            if len(r['rois'])==0:
                print('Nothing detected in image with id: '+ image_id)  